In [1]:
from google.colab import drive
drive.mount('/content/drive/')

Mounted at /content/drive/


In [2]:
!pip install sentencepiece

     |████████████████████████████████| 1.2MB 14.3MB/s 


In [3]:
%%capture
!pip install transformers

In [4]:
import torch
import numpy as np
import pandas as pd
import torch.nn as nn

import transformers
from sklearn.metrics import *
from transformers import AdamW
from tqdm.notebook import tqdm
from scipy.special import softmax
from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split as tts
from transformers import BertTokenizerFast, BertConfig, BertForSequenceClassification, AutoModel
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler

In [5]:
# Define the device
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')

#### Download

In [6]:
cd drive/My Drive/Colab Notebooks/experiments

/content/drive/My Drive/Colab Notebooks/experiments


In [7]:
# Download humor detection data
# Paper: https://arxiv.org/abs/2004.12765
data = pd.read_csv("data/moh-x.csv")
print("\nThere are", len(data), "sentences")

# Use the standard text/label columns
# Create labels: 1 --> humorous, 0 --> not humorous
#data = data.dropna()
data["label"] = data["label"].apply(int)
data.head()


There are 647 sentences


arg1  arg2  ... verb_idx label
0  knowledge   NaN  ...        1     1
1       cost   NaN  ...        1     1
2        tax   NaN  ...        4     1
3  immigrant   NaN  ...        4     1
4   interest   NaN  ...        4     1

[5 rows x 6 columns]

#### Split to training, validation and test



In [8]:
# Use a subset for quick experiments
#data = data[:10000]

# Split to train, val and test
train, test = tts(data[["sentence", "label"]], random_state=42, test_size=0.1)
train, val = tts(train, random_state=42, test_size=test.shape[0])

#### Tokenize and encode with BERT tokenizer

In [9]:
from transformers import XLMRobertaForSequenceClassification

output_dir = 'stockholm/xlm_code/mohx_xlmroberta/xlm-roberta_model_save'

print(output_dir)

stockholm/xlm_code/mohx_xlmroberta/xlm-roberta_model_save


In [10]:
from transformers import XLMRobertaTokenizer
import torch
# Load the BERT tokenizer.
print('Loading XLMRobertaTokenizer...')
bert_tokenizer = XLMRobertaTokenizer.from_pretrained(output_dir)
model_e = XLMRobertaForSequenceClassification.from_pretrained(output_dir, num_labels = 2, output_attentions = True, output_hidden_states = True,)

Loading XLMRobertaTokenizer...


Some weights of the model checkpoint at stockholm/xlm_code/mohx_xlmroberta/xlm-roberta_model_save were not used when initializing XLMRobertaForSequenceClassification: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
- This IS expected if you are initializing XLMRobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [11]:
MAX_LEN = 21 # This value could be set as 256, 512 etc.

encoded_instance = bert_tokenizer.encode_plus(
            train.iloc[0].sentence,
            truncation = True,                
            add_special_tokens = True,
            max_length = MAX_LEN,     
            pad_to_max_length = True,
            return_attention_mask = True,  
            return_tensors = 'pt' # return pytorch tensors
       )


encoded_instance

/usr/local/lib/python3.7/dist-packages/transformers/tokenization_utils_base.py:2111: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  FutureWarning,


{'input_ids': tensor([[    0,    87,   377,   653,    25,    18, 22113,   903, 13765,     6,
             5,     2,     1,     1,     1,     1,     1,     1,     1,     1,
             1]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0]])}

In [12]:
print("Original text:", train.iloc[0].sentence)
print("BERT BPEs:", bert_tokenizer.convert_ids_to_tokens(encoded_instance["input_ids"][0]))

Original text:  I ca n't buy this story .
BERT BPEs: ['<s>', '▁I', '▁ca', '▁n', "'", 't', '▁buy', '▁this', '▁story', '▁', '.', '</s>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>']


In [13]:
# Set max_len to the maximum length of the training data 
max_len = max([len(bert_tokenizer.encode(s)) for s in train.sentence.to_list()])
print("The maximum sentence length in training based on BERT BPEs is", max_len)

The maximum sentence length in training based on BERT BPEs is 25


In [14]:
# Tokenize and encode sentences in each set
x_train = bert_tokenizer.batch_encode_plus(
    train.sentence.tolist(),
    max_length = max_len,
    padding=True,
    truncation=True
)
x_val = bert_tokenizer.batch_encode_plus(
    val.sentence.tolist(),
    max_length = max_len,
    padding=True,
    truncation=True
)
x_test = bert_tokenizer.batch_encode_plus(
    test.sentence.tolist(),
    max_length = max_len,
    padding=True,
    truncation=True
)

In [15]:
# Convert lists to tensors in order to feed them to our PyTorch model
train_seq = torch.tensor(x_train['input_ids'])
train_mask = torch.tensor(x_train['attention_mask'])
train_y = torch.tensor(train.label.tolist())

val_seq = torch.tensor(x_val['input_ids'])
val_mask = torch.tensor(x_val['attention_mask'])
val_y = torch.tensor(val.label.tolist())

test_seq = torch.tensor(x_test['input_ids'])
test_mask = torch.tensor(x_test['attention_mask'])
test_y = torch.tensor(test.label.tolist())

In [16]:
batch_size = 32

# Create a dataloader for each set

# TensorDataset: Creates a PyTorch dataset object to load data from
train_data = TensorDataset(train_seq, train_mask, train_y)
# RandomSampler: specify the sequence of indices/keys used in data loading
train_sampler = RandomSampler(train_data)
# DataLoader: a Python iterable over a dataset
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=batch_size)

val_data = TensorDataset(val_seq, val_mask, val_y)
val_sampler = SequentialSampler(val_data)
val_dataloader = DataLoader(val_data, sampler=val_sampler, batch_size=batch_size)

test_data = TensorDataset(test_seq, test_mask, test_y)
test_sampler = SequentialSampler(test_data)
test_dataloader = DataLoader(test_data, sampler=test_sampler, batch_size=1)

## Inference

#### Load the saved checkpoint

In [17]:
model_e = model_e.to(device)

#### Get predictions for test

In [18]:
# Predict for the test set and save the results
model_e.eval()
test_predictions = []
test_targets = []
test_attentions = []
test_inputs = []

for batch in test_dataloader:
  batch = [t.to(device) for t in batch]
  sent_id, mask, labels = batch
  # Get gold labels
  test_targets.extend(labels.detach().cpu().numpy())
  # Get input words
  test_inputs.append(bert_tokenizer.convert_ids_to_tokens(sent_id.detach().cpu().numpy()[0]))
  with torch.no_grad():
    # Get predictions
    outputs = model_e(sent_id, attention_mask=mask)
    # Apply softmax to the outputs
    output_probs = softmax(outputs.logits.detach().cpu().numpy(), axis=1)
    # Get the with the highest probability as the predicted label
    test_predictions.extend(np.argmax(output_probs, axis=1))
    # Get attention weights
    # Attention weights from all layers are returned in a tuple
    # The weights from each layer are in a tensor with shape (batch_size, attention_heads, max_len, max_len)
    test_attentions.append(outputs.attentions)

#### Evaluate

In [19]:
print("F1:", f1_score(test_targets, test_predictions, average="binary"))
print("ACC:", accuracy_score(test_targets, test_predictions))
print("AUPR:", average_precision_score(test_targets, test_predictions))
print("PRECISION:", precision_score(test_targets, test_predictions))
print("RECALL:", recall_score(test_targets, test_predictions))
print("AUC:", roc_auc_score(test_targets, test_predictions))

F1: 0.8732394366197184
ACC: 0.8615384615384616
AUPR: 0.8396214896214896
PRECISION: 0.8857142857142857
RECALL: 0.8611111111111112
AUC: 0.8615900383141761


## Attention analysis


In [ ]:
# Get attention heatmaps
import matplotlib
from IPython.core.display import display, HTML
def colorize(words, color_array):
    cmap=matplotlib.cm.Reds
    template = '<span class="barcode"; style="color: black; background-color: {}">{}</span>'
    colored_string = ''
    for word, color in zip(words, color_array):
        color = matplotlib.colors.rgb2hex(cmap(color)[:3])
        colored_string += template.format(color, '&nbsp' + word + '&nbsp')
    return colored_string

In [ ]:
#max pooling to generate a fixed sized sentence embedding


#Max Pooling - Take the max value over time for every dimension
def max_pooling(model_output, attention_mask):
    token_embeddings = model_output[0] #First element of model_output contains all token embeddings
    input_mask_expanded = attention_mask.resize_(token_embeddings.size())
    #input_mask_expanded = attention_mask.unsqueeze(-1).expand(token_embeddings.size()).float()
    token_embeddings[input_mask_expanded == 0] = -1e9  # Set padding tokens to large negative value
    max_over_time = torch.max(token_embeddings, 1)[0]
    return max_over_time

def avg_pooling(model_output, attention_mask):
    token_embeddings = model_output[0] #First element of model_output contains all token embeddings
    input_mask_expanded = attention_mask.resize_(token_embeddings.size())
    #input_mask_expanded = attention_mask.unsqueeze(-1).expand(token_embeddings.size()).float()
    token_embeddings[input_mask_expanded == 0] = -1e9  # Set padding tokens to large negative value
    avg_over_time = torch.mean(token_embeddings, 1)[0]
    return avg_over_time


#Sentences we want sentence embeddings for
sentences = ['The', 'stars', 'gravitate', 'towards', 'each', 'other.']

#Tokenize sentences
encoded_input = bert_tokenizer(sentences, padding=True, truncation=True, max_length=128, return_tensors='pt')
encoded_input = encoded_input.to(device)

#Compute token embeddings
with torch.no_grad():
    model_output = model_e(**encoded_input)

#Perform pooling. In this case, max pooling
sentence_embeddings = max_pooling(model_output, encoded_input['attention_mask'])
#avg_sentence_embeddings = avg_pooling(model_output, encoded_input['attention_mask'])


print("Sentence embeddings:")
print(sentence_embeddings)

Sentence embeddings:
tensor([0.2211, 0.3184, 0.0814, 0.2717, 0.8786, 1.0564], device='cuda:0')


In [ ]:
# numpy implementation of argmax
from numpy import argmax

sentence_embeddings = sentence_embeddings.cpu()

# get argmax
result = argmax(sentence_embeddings)
print('arg max of %s: %d' % (sentence_embeddings, result))

arg max of tensor([0.2211, 0.3184, 0.0814, 0.2717, 0.8786, 1.0564]): 5


In [ ]:
#CLS token of each input represents the sentence embedding


#Sentences we want sentence embeddings for
sentences = ['The', 'stars', 'gravitate', 'towards', 'each', 'other']


#Tokenize sentences
encoded_input = bert_tokenizer(sentences, padding=True, truncation=True, max_length=128, return_tensors='pt')
encoded_input = encoded_input.to(device)

#Compute token embeddings
with torch.no_grad():
    model_output = model_e(**encoded_input)
    #model_output = model_output.to(device)
    
sentence_embeddings = model_output[0][:,0] #Take the first token ([CLS]) from each sentence 

print("Sentence embeddings:")
print(sentence_embeddings)

Sentence embeddings:
tensor([-0.2066,  0.3184, -0.0368,  0.2717,  0.8786, -0.4190], device='cuda:0')


In [ ]:
# numpy implementation of argmax
from numpy import argmax

sentence_embeddings = sentence_embeddings.cpu()

# get argmax
result = argmax(sentence_embeddings)
print('arg max of %s: %d' % (sentence_embeddings, result))

arg max of tensor([-0.2066,  0.3184, -0.0368,  0.2717,  0.8786, -0.4190]): 4


#### What does the CLS token attend to?




In [ ]:
# Original Loop

# Select some sentences randomly
sent_index = [0, 1, 2]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    for h, head in enumerate(attention):
      print("Head", h+1)
      # Get the attention for the cls token
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
    

****************************************************************************************************

Layer 1
Head 1


Head 2


Head 3


Head 4


Head 5


...

Head 8


Head 9


Head 10


Head 11


Head 12


In [ ]:
# Max Pooling for all tokens in sentences and argmax

# Select some sentences randomly
sent_index = [0,1,2,3,4,5,6,7,8,9,10]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, truncation=True, padding=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([ 0.0697, -0.4032,  0.5557, -0.0694,  0.5033, -0.3930,  0.2778, -0.0768,
         0.2889, -0.3930,  0.0308, -0.0643, -0.0010, -0.0650,  0.1977, -0.1437,
         0.1977, -0.1437,  0.1977, -0.1437,  0.1977])
arg max of tensor([ 0.0697, -0.4032,  0.5557, -0.0694,  0.5033, -0.3930,  0.2778, -0.0768,
         0.2889, -0.3930,  0.0308, -0.0643, -0.0010, -0.0650,  0.1977, -0.1437,
         0.1977, -0.1437,  0.1977, -0.1437,  0.1977]): 2

Layer 2


Tokens embeddings:
tensor([ 0.0697, -0.4032,  0.5557, -0.0694,  0.5033, -0.3930,  0.2778, -0.0768,
         0.2889, -0.3930,  0.0308, -0.0643, -0.0010, -0.0650,  0.1977, -0.1437,
         0.1977, -0.1437,  0.1977, -0.1437,  0.1977])
arg max of tensor([ 0.0697, -0.4032,  0.5557, -0.0694,  0.5033, -0.3930,  0.2778, -0.0768,
         0.2889, -0.3930,  0.0308, -0.0643, -0.0010, -0.0650,  0.1977, -0.1437,
         0.1977, -0.1437,  0.1977, -0.1437,  0.1977]): 2

Layer 3


Tokens embeddings:
tensor([ 0.0697, -0.4032,  0.5557, -0.0694,  0.5033, -0.3930,  0.2778, -0.0768,
         0.2889, -0.3930,  0.0308, -0.0643, -0.0010, -0.0650,  0.1977, -0.1437,
         0.1977, -0.1437,  0.1977, -0.1437,  0.1977])
arg max of tensor([ 0.0697, -0.4032,  0.5557, -0.0694,  0.5033, -0.3930,  0.2778, -0.0768,
         0.2889, -0.3930,  0.0308, -0.0643, -0.0010, -0.0650,  0.1977, -0.1437,
         0.1977, -0.1437,  0.1977, -0.1437,  0.1977]): 2

Layer 4


Tokens embeddings:
tensor([ 0.0697, -0.4032,  0.5557, -0.0694,  0.5033, -0.3930,  0.2778, -0.0768,
         0.2889, -0.3930,  0.0308, -0.0643, -0.0010, -0.0650,  0.1977, -0.1437,
         0.1977, -0.1437,  0.1977, -0.1437,  0.1977])
arg max of tensor([ 0.0697, -0.4032,  0.5557, -0.0694,  0.5033, -0.3930,  0.2778, -0.0768,
         0.2889, -0.3930,  0.0308, -0.0643, -0.0010, -0.0650,  0.1977, -0.1437,
         0.1977, -0.1437,  0.1977, -0.1437,  0.1977]): 2

Layer 5


...

Tokens embeddings:
tensor([ 6.9720e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04,  7.0138e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04,  7.0138e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01]): 8

Layer 9


Tokens embeddings:
tensor([ 6.9720e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04,  7.0138e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04,  7.0138e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01]): 8

Layer 10


Tokens embeddings:
tensor([ 6.9720e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04,  7.0138e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04,  7.0138e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01]): 8

Layer 11


Tokens embeddings:
tensor([ 6.9720e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04,  7.0138e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04,  7.0138e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01]): 8

Layer 12


Tokens embeddings:
tensor([ 6.9720e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04,  7.0138e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04,  7.0138e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01]): 8


In [ ]:
# Select some sentences randomly
sent_index = [11,12,13,14,15,16,17,18,19,20]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, truncation=True, padding=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([ 6.9720e-02, -2.0659e-01,  6.4695e-01,  6.0369e-02,  1.5846e-01,
         1.2314e-01,  5.7259e-01,  6.0280e-01,  1.1332e-01, -6.4283e-02,
        -9.5306e-04, -6.5009e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -2.0659e-01,  6.4695e-01,  6.0369e-02,  1.5846e-01,
         1.2314e-01,  5.7259e-01,  6.0280e-01,  1.1332e-01, -6.4283e-02,
        -9.5306e-04, -6.5009e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01]): 2

Layer 2


Tokens embeddings:
tensor([ 6.9720e-02, -2.0659e-01,  6.4695e-01,  6.0369e-02,  1.5846e-01,
         1.2314e-01,  5.7259e-01,  6.0280e-01,  1.1332e-01, -6.4283e-02,
        -9.5306e-04, -6.5009e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -2.0659e-01,  6.4695e-01,  6.0369e-02,  1.5846e-01,
         1.2314e-01,  5.7259e-01,  6.0280e-01,  1.1332e-01, -6.4283e-02,
        -9.5306e-04, -6.5009e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01]): 2

Layer 3


Tokens embeddings:
tensor([ 6.9720e-02, -2.0659e-01,  6.4695e-01,  6.0369e-02,  1.5846e-01,
         1.2314e-01,  5.7259e-01,  6.0280e-01,  1.1332e-01, -6.4283e-02,
        -9.5306e-04, -6.5009e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -2.0659e-01,  6.4695e-01,  6.0369e-02,  1.5846e-01,
         1.2314e-01,  5.7259e-01,  6.0280e-01,  1.1332e-01, -6.4283e-02,
        -9.5306e-04, -6.5009e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01]): 2

Layer 4


Tokens embeddings:
tensor([ 6.9720e-02, -2.0659e-01,  6.4695e-01,  6.0369e-02,  1.5846e-01,
         1.2314e-01,  5.7259e-01,  6.0280e-01,  1.1332e-01, -6.4283e-02,
        -9.5306e-04, -6.5009e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -2.0659e-01,  6.4695e-01,  6.0369e-02,  1.5846e-01,
         1.2314e-01,  5.7259e-01,  6.0280e-01,  1.1332e-01, -6.4283e-02,
        -9.5306e-04, -6.5009e-02,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01, -1.0000e+09,
         1.9772e-01]): 2

Layer 5


...

Tokens embeddings:
tensor([ 6.9720e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01,  1.1437e+00,
        -1.2175e-01,  2.5263e-01,  6.8802e-02, -9.5306e-04, -6.5009e-02,
         1.9772e-01, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.0000e+09,  1.9772e-01,  1.9772e-01,  1.9772e-01, -1.4367e-01,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01,  1.1437e+00,
        -1.2175e-01,  2.5263e-01,  6.8802e-02, -9.5306e-04, -6.5009e-02,
         1.9772e-01, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.0000e+09,  1.9772e-01,  1.9772e-01,  1.9772e-01, -1.4367e-01,
         1.9772e-01]): 4

Layer 9


Tokens embeddings:
tensor([ 6.9720e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01,  1.1437e+00,
        -1.2175e-01,  2.5263e-01,  6.8802e-02, -9.5306e-04, -6.5009e-02,
         1.9772e-01, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.0000e+09,  1.9772e-01,  1.9772e-01,  1.9772e-01, -1.4367e-01,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01,  1.1437e+00,
        -1.2175e-01,  2.5263e-01,  6.8802e-02, -9.5306e-04, -6.5009e-02,
         1.9772e-01, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.0000e+09,  1.9772e-01,  1.9772e-01,  1.9772e-01, -1.4367e-01,
         1.9772e-01]): 4

Layer 10


Tokens embeddings:
tensor([ 6.9720e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01,  1.1437e+00,
        -1.2175e-01,  2.5263e-01,  6.8802e-02, -9.5306e-04, -6.5009e-02,
         1.9772e-01, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.0000e+09,  1.9772e-01,  1.9772e-01,  1.9772e-01, -1.4367e-01,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01,  1.1437e+00,
        -1.2175e-01,  2.5263e-01,  6.8802e-02, -9.5306e-04, -6.5009e-02,
         1.9772e-01, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.0000e+09,  1.9772e-01,  1.9772e-01,  1.9772e-01, -1.4367e-01,
         1.9772e-01]): 4

Layer 11


Tokens embeddings:
tensor([ 6.9720e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01,  1.1437e+00,
        -1.2175e-01,  2.5263e-01,  6.8802e-02, -9.5306e-04, -6.5009e-02,
         1.9772e-01, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.0000e+09,  1.9772e-01,  1.9772e-01,  1.9772e-01, -1.4367e-01,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01,  1.1437e+00,
        -1.2175e-01,  2.5263e-01,  6.8802e-02, -9.5306e-04, -6.5009e-02,
         1.9772e-01, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.0000e+09,  1.9772e-01,  1.9772e-01,  1.9772e-01, -1.4367e-01,
         1.9772e-01]): 4

Layer 12


Tokens embeddings:
tensor([ 6.9720e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01,  1.1437e+00,
        -1.2175e-01,  2.5263e-01,  6.8802e-02, -9.5306e-04, -6.5009e-02,
         1.9772e-01, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.0000e+09,  1.9772e-01,  1.9772e-01,  1.9772e-01, -1.4367e-01,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01,  1.1437e+00,
        -1.2175e-01,  2.5263e-01,  6.8802e-02, -9.5306e-04, -6.5009e-02,
         1.9772e-01, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.0000e+09,  1.9772e-01,  1.9772e-01,  1.9772e-01, -1.4367e-01,
         1.9772e-01]): 4


In [ ]:
# Max Pooling for all tokens in sentences and argmax

# Select some sentences randomly
sent_index = [21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, truncation=True, padding=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([ 6.9720e-02, -2.9882e-01,  3.7319e-01,  8.8741e-02,  7.4797e-02,
        -1.0577e+00,  1.1827e+00,  9.4951e-02,  1.2176e+00, -2.0302e-01,
        -8.6322e-02,  8.8741e-02,  4.4967e-01, -7.6757e-02,  1.1437e+00,
         7.1513e-02,  6.8802e-02, -9.5306e-04,  7.0138e-02, -1.4367e-01,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -2.9882e-01,  3.7319e-01,  8.8741e-02,  7.4797e-02,
        -1.0577e+00,  1.1827e+00,  9.4951e-02,  1.2176e+00, -2.0302e-01,
        -8.6322e-02,  8.8741e-02,  4.4967e-01, -7.6757e-02,  1.1437e+00,
         7.1513e-02,  6.8802e-02, -9.5306e-04,  7.0138e-02, -1.4367e-01,
         1.9772e-01]): 8

Layer 2


Tokens embeddings:
tensor([ 6.9720e-02, -2.9882e-01,  3.7319e-01,  8.8741e-02,  7.4797e-02,
        -1.0577e+00,  1.1827e+00,  9.4951e-02,  1.2176e+00, -2.0302e-01,
        -8.6322e-02,  8.8741e-02,  4.4967e-01, -7.6757e-02,  1.1437e+00,
         7.1513e-02,  6.8802e-02, -9.5306e-04,  7.0138e-02, -1.4367e-01,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -2.9882e-01,  3.7319e-01,  8.8741e-02,  7.4797e-02,
        -1.0577e+00,  1.1827e+00,  9.4951e-02,  1.2176e+00, -2.0302e-01,
        -8.6322e-02,  8.8741e-02,  4.4967e-01, -7.6757e-02,  1.1437e+00,
         7.1513e-02,  6.8802e-02, -9.5306e-04,  7.0138e-02, -1.4367e-01,
         1.9772e-01]): 8

Layer 3


Tokens embeddings:
tensor([ 6.9720e-02, -2.9882e-01,  3.7319e-01,  8.8741e-02,  7.4797e-02,
        -1.0577e+00,  1.1827e+00,  9.4951e-02,  1.2176e+00, -2.0302e-01,
        -8.6322e-02,  8.8741e-02,  4.4967e-01, -7.6757e-02,  1.1437e+00,
         7.1513e-02,  6.8802e-02, -9.5306e-04,  7.0138e-02, -1.4367e-01,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -2.9882e-01,  3.7319e-01,  8.8741e-02,  7.4797e-02,
        -1.0577e+00,  1.1827e+00,  9.4951e-02,  1.2176e+00, -2.0302e-01,
        -8.6322e-02,  8.8741e-02,  4.4967e-01, -7.6757e-02,  1.1437e+00,
         7.1513e-02,  6.8802e-02, -9.5306e-04,  7.0138e-02, -1.4367e-01,
         1.9772e-01]): 8

Layer 4


Tokens embeddings:
tensor([ 6.9720e-02, -2.9882e-01,  3.7319e-01,  8.8741e-02,  7.4797e-02,
        -1.0577e+00,  1.1827e+00,  9.4951e-02,  1.2176e+00, -2.0302e-01,
        -8.6322e-02,  8.8741e-02,  4.4967e-01, -7.6757e-02,  1.1437e+00,
         7.1513e-02,  6.8802e-02, -9.5306e-04,  7.0138e-02, -1.4367e-01,
         1.9772e-01])
arg max of tensor([ 6.9720e-02, -2.9882e-01,  3.7319e-01,  8.8741e-02,  7.4797e-02,
        -1.0577e+00,  1.1827e+00,  9.4951e-02,  1.2176e+00, -2.0302e-01,
        -8.6322e-02,  8.8741e-02,  4.4967e-01, -7.6757e-02,  1.1437e+00,
         7.1513e-02,  6.8802e-02, -9.5306e-04,  7.0138e-02, -1.4367e-01,
         1.9772e-01]): 8

Layer 5


...

Tokens embeddings:
tensor([ 6.9720e-02,  5.3506e-03,  7.9953e-01,  7.0165e-01, -1.5160e-02,
         2.3438e-01,  1.7266e-01, -1.3025e-01,  6.8802e-02, -9.5306e-04,
         7.0138e-02, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.0000e+09,  1.9772e-01,  1.9772e-01,
         1.9772e-01])
arg max of tensor([ 6.9720e-02,  5.3506e-03,  7.9953e-01,  7.0165e-01, -1.5160e-02,
         2.3438e-01,  1.7266e-01, -1.3025e-01,  6.8802e-02, -9.5306e-04,
         7.0138e-02, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.0000e+09,  1.9772e-01,  1.9772e-01,
         1.9772e-01]): 2

Layer 9


Tokens embeddings:
tensor([ 6.9720e-02,  5.3506e-03,  7.9953e-01,  7.0165e-01, -1.5160e-02,
         2.3438e-01,  1.7266e-01, -1.3025e-01,  6.8802e-02, -9.5306e-04,
         7.0138e-02, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.0000e+09,  1.9772e-01,  1.9772e-01,
         1.9772e-01])
arg max of tensor([ 6.9720e-02,  5.3506e-03,  7.9953e-01,  7.0165e-01, -1.5160e-02,
         2.3438e-01,  1.7266e-01, -1.3025e-01,  6.8802e-02, -9.5306e-04,
         7.0138e-02, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.0000e+09,  1.9772e-01,  1.9772e-01,
         1.9772e-01]): 2

Layer 10


Tokens embeddings:
tensor([ 6.9720e-02,  5.3506e-03,  7.9953e-01,  7.0165e-01, -1.5160e-02,
         2.3438e-01,  1.7266e-01, -1.3025e-01,  6.8802e-02, -9.5306e-04,
         7.0138e-02, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.0000e+09,  1.9772e-01,  1.9772e-01,
         1.9772e-01])
arg max of tensor([ 6.9720e-02,  5.3506e-03,  7.9953e-01,  7.0165e-01, -1.5160e-02,
         2.3438e-01,  1.7266e-01, -1.3025e-01,  6.8802e-02, -9.5306e-04,
         7.0138e-02, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.0000e+09,  1.9772e-01,  1.9772e-01,
         1.9772e-01]): 2

Layer 11


Tokens embeddings:
tensor([ 6.9720e-02,  5.3506e-03,  7.9953e-01,  7.0165e-01, -1.5160e-02,
         2.3438e-01,  1.7266e-01, -1.3025e-01,  6.8802e-02, -9.5306e-04,
         7.0138e-02, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.0000e+09,  1.9772e-01,  1.9772e-01,
         1.9772e-01])
arg max of tensor([ 6.9720e-02,  5.3506e-03,  7.9953e-01,  7.0165e-01, -1.5160e-02,
         2.3438e-01,  1.7266e-01, -1.3025e-01,  6.8802e-02, -9.5306e-04,
         7.0138e-02, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.0000e+09,  1.9772e-01,  1.9772e-01,
         1.9772e-01]): 2

Layer 12


Tokens embeddings:
tensor([ 6.9720e-02,  5.3506e-03,  7.9953e-01,  7.0165e-01, -1.5160e-02,
         2.3438e-01,  1.7266e-01, -1.3025e-01,  6.8802e-02, -9.5306e-04,
         7.0138e-02, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.0000e+09,  1.9772e-01,  1.9772e-01,
         1.9772e-01])
arg max of tensor([ 6.9720e-02,  5.3506e-03,  7.9953e-01,  7.0165e-01, -1.5160e-02,
         2.3438e-01,  1.7266e-01, -1.3025e-01,  6.8802e-02, -9.5306e-04,
         7.0138e-02, -1.4367e-01,  1.9772e-01, -1.4367e-01,  1.9772e-01,
        -1.4367e-01,  1.9772e-01, -1.0000e+09,  1.9772e-01,  1.9772e-01,
         1.9772e-01]): 2


In [ ]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    for h, head in enumerate(attention):
      print("Head", h+1)
      # Get the attention for the cls token
      encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
      encoded_tokens = encoded_tokens.to(device)
      with torch.no_grad():
        model_output1 = model_e(**encoded_tokens)
        tokens_embeddings = model_output1[0][:,0]
        tokens_embeddings = tokens_embeddings.cpu()
        cls_attentions = head[0]
        display(HTML(colorize(tokens, cls_attentions)))
        print("Tokens embeddings:")
        print(tokens_embeddings)
        arg = argmax(tokens_embeddings)
        print('arg max of %s: %d' % (tokens_embeddings, arg))

In [ ]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #for h, head in enumerate(attention):
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = model_output1[0][:,0]
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([-0.0646, -0.4032,  0.5557, -0.0694, -0.3240, -0.3930,  0.2778, -0.0768,
        -0.2023, -0.3930, -0.0597, -0.0643, -0.0010, -0.0650, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437])
arg max of tensor([-0.0646, -0.4032,  0.5557, -0.0694, -0.3240, -0.3930,  0.2778, -0.0768,
        -0.2023, -0.3930, -0.0597, -0.0643, -0.0010, -0.0650, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437]): 2

Layer 2


Tokens embeddings:
tensor([-0.0646, -0.4032,  0.5557, -0.0694, -0.3240, -0.3930,  0.2778, -0.0768,
        -0.2023, -0.3930, -0.0597, -0.0643, -0.0010, -0.0650, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437])
arg max of tensor([-0.0646, -0.4032,  0.5557, -0.0694, -0.3240, -0.3930,  0.2778, -0.0768,
        -0.2023, -0.3930, -0.0597, -0.0643, -0.0010, -0.0650, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437]): 2

Layer 3


Tokens embeddings:
tensor([-0.0646, -0.4032,  0.5557, -0.0694, -0.3240, -0.3930,  0.2778, -0.0768,
        -0.2023, -0.3930, -0.0597, -0.0643, -0.0010, -0.0650, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437])
arg max of tensor([-0.0646, -0.4032,  0.5557, -0.0694, -0.3240, -0.3930,  0.2778, -0.0768,
        -0.2023, -0.3930, -0.0597, -0.0643, -0.0010, -0.0650, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437]): 2

Layer 4


Tokens embeddings:
tensor([-0.0646, -0.4032,  0.5557, -0.0694, -0.3240, -0.3930,  0.2778, -0.0768,
        -0.2023, -0.3930, -0.0597, -0.0643, -0.0010, -0.0650, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437])
arg max of tensor([-0.0646, -0.4032,  0.5557, -0.0694, -0.3240, -0.3930,  0.2778, -0.0768,
        -0.2023, -0.3930, -0.0597, -0.0643, -0.0010, -0.0650, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437]): 2

Layer 5


...

Tokens embeddings:
tensor([-6.4571e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04, -6.5009e-02, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01])
arg max of tensor([-6.4571e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04, -6.5009e-02, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01]): 8

Layer 9


Tokens embeddings:
tensor([-6.4571e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04, -6.5009e-02, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01])
arg max of tensor([-6.4571e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04, -6.5009e-02, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01]): 8

Layer 10


Tokens embeddings:
tensor([-6.4571e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04, -6.5009e-02, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01])
arg max of tensor([-6.4571e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04, -6.5009e-02, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01]): 8

Layer 11


Tokens embeddings:
tensor([-6.4571e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04, -6.5009e-02, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01])
arg max of tensor([-6.4571e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04, -6.5009e-02, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01]): 8

Layer 12


Tokens embeddings:
tensor([-6.4571e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04, -6.5009e-02, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01])
arg max of tensor([-6.4571e-02, -6.3919e-02, -1.5160e-02, -6.1332e-01,  5.8607e-01,
         9.4284e-01,  1.2314e-01, -3.9304e-01,  1.3893e+00, -6.4283e-02,
        -9.5306e-04, -6.5009e-02, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01]): 8


In [ ]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [11, 12, 13, 14, 15, 16, 17, 18, 19, 20]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #for h, head in enumerate(attention):
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = model_output1[0][:,0]
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([-0.0646, -0.2066,  0.6469,  0.0604, -0.1177,  0.1231,  0.5726,  0.6028,
        -0.0811, -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437])
arg max of tensor([-0.0646, -0.2066,  0.6469,  0.0604, -0.1177,  0.1231,  0.5726,  0.6028,
        -0.0811, -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437]): 2

Layer 2


Tokens embeddings:
tensor([-0.0646, -0.2066,  0.6469,  0.0604, -0.1177,  0.1231,  0.5726,  0.6028,
        -0.0811, -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437])
arg max of tensor([-0.0646, -0.2066,  0.6469,  0.0604, -0.1177,  0.1231,  0.5726,  0.6028,
        -0.0811, -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437]): 2

Layer 3


Tokens embeddings:
tensor([-0.0646, -0.2066,  0.6469,  0.0604, -0.1177,  0.1231,  0.5726,  0.6028,
        -0.0811, -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437])
arg max of tensor([-0.0646, -0.2066,  0.6469,  0.0604, -0.1177,  0.1231,  0.5726,  0.6028,
        -0.0811, -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437]): 2

Layer 4


Tokens embeddings:
tensor([-0.0646, -0.2066,  0.6469,  0.0604, -0.1177,  0.1231,  0.5726,  0.6028,
        -0.0811, -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437])
arg max of tensor([-0.0646, -0.2066,  0.6469,  0.0604, -0.1177,  0.1231,  0.5726,  0.6028,
        -0.0811, -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437]): 2

Layer 5


...

Tokens embeddings:
tensor([-6.4571e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01, -1.0577e+00,
        -1.2175e-01, -2.0340e-01, -6.4283e-02, -9.5306e-04, -6.5009e-02,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01])
arg max of tensor([-6.4571e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01, -1.0577e+00,
        -1.2175e-01, -2.0340e-01, -6.4283e-02, -9.5306e-04, -6.5009e-02,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01]): 3

Layer 9


Tokens embeddings:
tensor([-6.4571e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01, -1.0577e+00,
        -1.2175e-01, -2.0340e-01, -6.4283e-02, -9.5306e-04, -6.5009e-02,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01])
arg max of tensor([-6.4571e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01, -1.0577e+00,
        -1.2175e-01, -2.0340e-01, -6.4283e-02, -9.5306e-04, -6.5009e-02,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01]): 3

Layer 10


Tokens embeddings:
tensor([-6.4571e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01, -1.0577e+00,
        -1.2175e-01, -2.0340e-01, -6.4283e-02, -9.5306e-04, -6.5009e-02,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01])
arg max of tensor([-6.4571e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01, -1.0577e+00,
        -1.2175e-01, -2.0340e-01, -6.4283e-02, -9.5306e-04, -6.5009e-02,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01]): 3

Layer 11


Tokens embeddings:
tensor([-6.4571e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01, -1.0577e+00,
        -1.2175e-01, -2.0340e-01, -6.4283e-02, -9.5306e-04, -6.5009e-02,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01])
arg max of tensor([-6.4571e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01, -1.0577e+00,
        -1.2175e-01, -2.0340e-01, -6.4283e-02, -9.5306e-04, -6.5009e-02,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01]): 3

Layer 12


Tokens embeddings:
tensor([-6.4571e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01, -1.0577e+00,
        -1.2175e-01, -2.0340e-01, -6.4283e-02, -9.5306e-04, -6.5009e-02,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01])
arg max of tensor([-6.4571e-02, -4.0320e-01,  2.0520e-01,  3.9382e-01, -1.0577e+00,
        -1.2175e-01, -2.0340e-01, -6.4283e-02, -9.5306e-04, -6.5009e-02,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01, -1.4367e-01,
        -1.4367e-01]): 3


In [ ]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #for h, head in enumerate(attention):
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = model_output1[0][:,0]
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([-6.4571e-02, -2.9882e-01, -2.6628e-01,  8.8741e-02, -5.2115e-02,
        -1.0577e+00, -8.6423e-01,  9.4951e-02, -9.7911e-01, -2.0302e-01,
        -1.3025e-01,  8.8741e-02, -3.3548e-01, -7.6757e-02, -1.0577e+00,
         7.1513e-02, -6.4283e-02, -9.5306e-04, -6.5009e-02, -1.4367e-01,
        -1.4367e-01])
arg max of tensor([-6.4571e-02, -2.9882e-01, -2.6628e-01,  8.8741e-02, -5.2115e-02,
        -1.0577e+00, -8.6423e-01,  9.4951e-02, -9.7911e-01, -2.0302e-01,
        -1.3025e-01,  8.8741e-02, -3.3548e-01, -7.6757e-02, -1.0577e+00,
         7.1513e-02, -6.4283e-02, -9.5306e-04, -6.5009e-02, -1.4367e-01,
        -1.4367e-01]): 7

Layer 2


Tokens embeddings:
tensor([-6.4571e-02, -2.9882e-01, -2.6628e-01,  8.8741e-02, -5.2115e-02,
        -1.0577e+00, -8.6423e-01,  9.4951e-02, -9.7911e-01, -2.0302e-01,
        -1.3025e-01,  8.8741e-02, -3.3548e-01, -7.6757e-02, -1.0577e+00,
         7.1513e-02, -6.4283e-02, -9.5306e-04, -6.5009e-02, -1.4367e-01,
        -1.4367e-01])
arg max of tensor([-6.4571e-02, -2.9882e-01, -2.6628e-01,  8.8741e-02, -5.2115e-02,
        -1.0577e+00, -8.6423e-01,  9.4951e-02, -9.7911e-01, -2.0302e-01,
        -1.3025e-01,  8.8741e-02, -3.3548e-01, -7.6757e-02, -1.0577e+00,
         7.1513e-02, -6.4283e-02, -9.5306e-04, -6.5009e-02, -1.4367e-01,
        -1.4367e-01]): 7

Layer 3


Tokens embeddings:
tensor([-6.4571e-02, -2.9882e-01, -2.6628e-01,  8.8741e-02, -5.2115e-02,
        -1.0577e+00, -8.6423e-01,  9.4951e-02, -9.7911e-01, -2.0302e-01,
        -1.3025e-01,  8.8741e-02, -3.3548e-01, -7.6757e-02, -1.0577e+00,
         7.1513e-02, -6.4283e-02, -9.5306e-04, -6.5009e-02, -1.4367e-01,
        -1.4367e-01])
arg max of tensor([-6.4571e-02, -2.9882e-01, -2.6628e-01,  8.8741e-02, -5.2115e-02,
        -1.0577e+00, -8.6423e-01,  9.4951e-02, -9.7911e-01, -2.0302e-01,
        -1.3025e-01,  8.8741e-02, -3.3548e-01, -7.6757e-02, -1.0577e+00,
         7.1513e-02, -6.4283e-02, -9.5306e-04, -6.5009e-02, -1.4367e-01,
        -1.4367e-01]): 7

Layer 4


Tokens embeddings:
tensor([-6.4571e-02, -2.9882e-01, -2.6628e-01,  8.8741e-02, -5.2115e-02,
        -1.0577e+00, -8.6423e-01,  9.4951e-02, -9.7911e-01, -2.0302e-01,
        -1.3025e-01,  8.8741e-02, -3.3548e-01, -7.6757e-02, -1.0577e+00,
         7.1513e-02, -6.4283e-02, -9.5306e-04, -6.5009e-02, -1.4367e-01,
        -1.4367e-01])
arg max of tensor([-6.4571e-02, -2.9882e-01, -2.6628e-01,  8.8741e-02, -5.2115e-02,
        -1.0577e+00, -8.6423e-01,  9.4951e-02, -9.7911e-01, -2.0302e-01,
        -1.3025e-01,  8.8741e-02, -3.3548e-01, -7.6757e-02, -1.0577e+00,
         7.1513e-02, -6.4283e-02, -9.5306e-04, -6.5009e-02, -1.4367e-01,
        -1.4367e-01]): 7

Layer 5


...

Tokens embeddings:
tensor([-0.0646,  0.0054,  0.7995,  0.7017, -0.0152,  0.2344,  0.1727, -0.1302,
        -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437])
arg max of tensor([-0.0646,  0.0054,  0.7995,  0.7017, -0.0152,  0.2344,  0.1727, -0.1302,
        -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437]): 2

Layer 9


Tokens embeddings:
tensor([-0.0646,  0.0054,  0.7995,  0.7017, -0.0152,  0.2344,  0.1727, -0.1302,
        -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437])
arg max of tensor([-0.0646,  0.0054,  0.7995,  0.7017, -0.0152,  0.2344,  0.1727, -0.1302,
        -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437]): 2

Layer 10


Tokens embeddings:
tensor([-0.0646,  0.0054,  0.7995,  0.7017, -0.0152,  0.2344,  0.1727, -0.1302,
        -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437])
arg max of tensor([-0.0646,  0.0054,  0.7995,  0.7017, -0.0152,  0.2344,  0.1727, -0.1302,
        -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437]): 2

Layer 11


Tokens embeddings:
tensor([-0.0646,  0.0054,  0.7995,  0.7017, -0.0152,  0.2344,  0.1727, -0.1302,
        -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437])
arg max of tensor([-0.0646,  0.0054,  0.7995,  0.7017, -0.0152,  0.2344,  0.1727, -0.1302,
        -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437]): 2

Layer 12


Tokens embeddings:
tensor([-0.0646,  0.0054,  0.7995,  0.7017, -0.0152,  0.2344,  0.1727, -0.1302,
        -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437])
arg max of tensor([-0.0646,  0.0054,  0.7995,  0.7017, -0.0152,  0.2344,  0.1727, -0.1302,
        -0.0643, -0.0010, -0.0650, -0.1437, -0.1437, -0.1437, -0.1437, -0.1437,
        -0.1437, -0.1437, -0.1437, -0.1437, -0.1437]): 2


#### Visualize attentions for specific types of grammatical errors

In [ ]:
# Lack of Subject-Verb Agreement
sentence1 = "I wrestled with this decision for years ."
# Pronoun Disagreement
sentence2 = "lined books are more enduring ."

In [ ]:
# Encode the first sentence
encoded_sentence1 = bert_tokenizer.batch_encode_plus([sentence1], padding=True)

# Give as input to the model and get the outputs
inputs = torch.tensor(encoded_sentence1["input_ids"]).to(device)
att = torch.tensor(encoded_sentence1["attention_mask"]).to(device)
outputs = model_e(inputs, attention_mask=att)

In [ ]:
# Get the predictions
output_probs = softmax(outputs.logits.detach().cpu().numpy(), axis=1)
predictions = (np.argmax(output_probs, axis=1))
print(sentence1, ":", predictions[0])

I wrestled with this decision for years . : 1


In [ ]:
# Visualize the attention heatmaps for the CLS token
tokens = bert_tokenizer.convert_ids_to_tokens(inputs.detach().cpu().numpy()[0])
for l in range(12):
  print("\nLayer", l+1)
  attention = np.squeeze(outputs.attentions[l].detach().cpu().numpy(), axis=0)
  cls_attentions = []
  for h, head in enumerate(attention):
    print("Head", h+1)
    # Get the attention for the cls token
    cls_attentions = head[0]
    display(HTML(colorize(tokens, cls_attentions)))


Layer 1
Head 1


Head 2


Head 3


Head 4


Head 5


...

Head 8


Head 9


Head 10


Head 11


Head 12


In [ ]:
# Encode the second sentence
encoded_sentence2 = bert_tokenizer.batch_encode_plus([sentence2], padding=True)

# Give as input to the model and get the outputs
inputs = torch.tensor(encoded_sentence2["input_ids"]).to(device)
att = torch.tensor(encoded_sentence2["attention_mask"]).to(device)
outputs = model_e(inputs, attention_mask=att)

# Get the predictions
output_probs = softmax(outputs.logits.detach().cpu().numpy(), axis=1)
predictions = (np.argmax(output_probs, axis=1))
print(sentence2, ":", predictions[0])

lined books are more enduring . : 1


In [ ]:
# Visualize the attention heatmaps for the CLS token
tokens = bert_tokenizer.convert_ids_to_tokens(inputs.detach().cpu().numpy()[0])
for l in range(12):
  print("\nLayer", l+1)
  attention = np.squeeze(outputs.attentions[l].detach().cpu().numpy(), axis=0)
  cls_attentions = []
  for h, head in enumerate(attention):
    print("Head", h+1)
    # Get the attention for the cls token
    cls_attentions = head[0]
    display(HTML(colorize(tokens, cls_attentions)))


Layer 1
Head 1


Head 2


Head 3


Head 4


Head 5


...

Head 8


Head 9


Head 10


Head 11


Head 12
